In [1]:
import pandas as pd
import datetime as dt
from datetime import date,time,datetime
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import MultiLabelBinarizer
import numpy as np
import pickle as pk
import os
import re
import nltk
from nltk.stem.snowball import SnowballStemmer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import string

In [2]:
!pwd

/home/akshara/coding/Phenotyping/preprocess


In [3]:
data_dir = "./mimic-iii"
files_dir = "../dump_files"

In [51]:
pheno = pd.read_csv(os.path.join(files_dir, 'PHENOTYPE.csv'))

In [52]:
pheno

HADM_ID  SUBJECT_ID  ROW_ID  ADVANCED.CANCER  ADVANCED.HEART.DISEASE  \
0      100103        3365   17170                0                       0   
1      100103        3365   17170                0                       0   
2      100137       27290   50828                0                       0   
3      100137       27290   50828                0                       0   
4      100473        5525   52670                0                       0   
...       ...         ...     ...              ...                     ...   
2271   199807       23549    2787                0                       1   
2272   199883        7029   18731                0                       0   
2273   199883        7029   18731                0                       0   
2274   199884        1931    8180                0                       1   
2275   199884        1931    8180                0                       1   

      ADVANCED.LUNG.DISEASE  ALCOHOL.ABUSE BATCH.ID  \
0                         0              0  08Apr16   
1                         0              0  08Apr16   
2                         0              0  08Apr16   
3                         0              0  08Apr16   
4                         0              0  18Feb16   
...                     ...            ...      ...   
2271                      1              0  07Dec15   
2272                      0              1  18Feb16   
2273                      0              1  18Feb16   
2274                      0              0  16Mar16   
2275                      0              0  16Mar16   

      CHRONIC.NEUROLOGICAL.DYSTROPHIES  CHRONIC.PAIN.FIBROMYALGIA  DEMENTIA  \
0                                    0                          0         0   
1                                    0                          0         0   
2                                    0                          0         0   
3                                    0                          0         0   
4                                    0                          0         0   
...                                ...                        ...       ...   
2271                                 0                          0         0   
2272                                 0                          0         0   
2273                                 0                          0         0   
2274                                 0                          0         0   
2275                                 0                          0         0   

      DEPRESSION  DEVELOPMENTAL.DELAY.RETARDATION  NON.ADHERENCE  NONE  \
0              0                                0              0     1   
1              0                                0              0     1   
2              0                                0              0     1   
3              0                                0              0     1   
4              0                                0              0     1   
...          ...                              ...            ...   ...   
2271           0                                0              0     0   
2272           0                                0              1     0   
2273           0                                0              1     0   
2274           1                                0              0     0   
2275           1                                0              0     0   

      OBESITY OPERATOR  OTHER.SUBSTANCE.ABUSE  \
0           0      JTW                      0   
1           0      ETM                      0   
2           0       JF                      0   
3           0       JW                      0   
4           0       JW                      0   
...       ...      ...                    ...   
2271        0      ETM                      0   
2272        0       JW                      0   
2273        0       JF                      0   
2274        0      DAG                      0   
2275        0       JW         

In [47]:
pheno.columns


Index(['HADM_ID', 'SUBJECT_ID', 'ROW_ID', 'ADVANCED.CANCER',
       'ADVANCED.HEART.DISEASE', 'ADVANCED.LUNG.DISEASE', 'ALCOHOL.ABUSE',
       'BATCH.ID', 'CHRONIC.NEUROLOGICAL.DYSTROPHIES',
       'CHRONIC.PAIN.FIBROMYALGIA', 'DEMENTIA', 'DEPRESSION',
       'DEVELOPMENTAL.DELAY.RETARDATION', 'NON.ADHERENCE', 'NONE', 'OBESITY',
       'OPERATOR', 'OTHER.SUBSTANCE.ABUSE',
       'SCHIZOPHRENIA.AND.OTHER.PSYCHIATRIC.DISORDERS', 'UNSURE'],
      dtype='object')

In [48]:
pheno  = pheno.drop(['subject.id', 'chart.time', 'cohort','Unsure','Non.Adherence','Dementia','Developmental.Delay.Retardation'], axis=1)

KeyError: "['subject.id' 'chart.time' 'cohort' 'Unsure' 'Non.Adherence' 'Dementia'\n 'Developmental.Delay.Retardation'] not found in axis"

In [ ]:
pheno.columns

In [49]:
pheno


HADM_ID  SUBJECT_ID  ROW_ID  ADVANCED.CANCER  ADVANCED.HEART.DISEASE  \
0      100103        3365   17170                0                       0   
1      100103        3365   17170                0                       0   
2      100137       27290   50828                0                       0   
3      100137       27290   50828                0                       0   
4      100473        5525   52670                0                       0   
...       ...         ...     ...              ...                     ...   
2271   199807       23549    2787                0                       1   
2272   199883        7029   18731                0                       0   
2273   199883        7029   18731                0                       0   
2274   199884        1931    8180                0                       1   
2275   199884        1931    8180                0                       1   

      ADVANCED.LUNG.DISEASE  ALCOHOL.ABUSE BATCH.ID  \
0                         0              0  08Apr16   
1                         0              0  08Apr16   
2                         0              0  08Apr16   
3                         0              0  08Apr16   
4                         0              0  18Feb16   
...                     ...            ...      ...   
2271                      1              0  07Dec15   
2272                      0              1  18Feb16   
2273                      0              1  18Feb16   
2274                      0              0  16Mar16   
2275                      0              0  16Mar16   

      CHRONIC.NEUROLOGICAL.DYSTROPHIES  CHRONIC.PAIN.FIBROMYALGIA  DEMENTIA  \
0                                    0                          0         0   
1                                    0                          0         0   
2                                    0                          0         0   
3                                    0                          0         0   
4                                    0                          0         0   
...                                ...                        ...       ...   
2271                                 0                          0         0   
2272                                 0                          0         0   
2273                                 0                          0         0   
2274                                 0                          0         0   
2275                                 0                          0         0   

      DEPRESSION  DEVELOPMENTAL.DELAY.RETARDATION  NON.ADHERENCE  NONE  \
0              0                                0              0     1   
1              0                                0              0     1   
2              0                                0              0     1   
3              0                                0              0     1   
4              0                                0              0     1   
...          ...                              ...            ...   ...   
2271           0                                0              0     0   
2272           0                                0              1     0   
2273           0                                0              1     0   
2274           1                                0              0     0   
2275           1                                0              0     0   

      OBESITY OPERATOR  OTHER.SUBSTANCE.ABUSE  \
0           0      JTW                      0   
1           0      ETM                      0   
2           0       JF                      0   
3           0       JW                      0   
4           0       JW                      0   
...       ...      ...                    ...   
2271        0      ETM                      0   
2272        0       JW                      0   
2273        0       JF                      0   
2274        0      DAG                      0   
2275        0       JW         

In [10]:
pheno.nunique(axis=0)

Hospital.Admission.ID                            1561
Obesity                                             2
Advanced.Heart.Disease                              2
Advanced.Lung.Disease                               2
Schizophrenia.and.other.Psychiatric.Disorders       2
Alcohol.Abuse                                       2
Other.Substance.Abuse                               2
Chronic.Pain.Fibromyalgia                           2
Chronic.Neurological.Dystrophies                    2
Advanced.Cancer                                     2
Depression                                          2
dtype: int64

pheno = pheno.groupby('HADM_ID').max().reset_index()

In [11]:
rad = pd.read_csv(os.path.join(files_dir, 'notes_rad.csv'))

In [12]:
pis = pd.read_csv(os.path.join(files_dir, 'notes_phys.csv'))

In [13]:
nurse = pd.read_csv(os.path.join(files_dir, 'notes_nurse.csv'))

In [14]:
rad.shape

(45526, 2)

In [15]:
pis.shape

(8983, 2)

In [16]:
nurse.shape

(9070, 2)

In [17]:
pheno.rename(columns={'Hospital.Admission.ID':'HADM_ID'}, inplace=True)

In [19]:
pheno.columns

Index(['HADM_ID', 'Obesity', 'Advanced.Heart.Disease', 'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression'],
      dtype='object')

In [20]:
rad_df = pheno.merge(rad, on='HADM_ID')

In [21]:
pis_df = pheno.merge(pis, on='HADM_ID')

In [22]:
nurse_df = pheno.merge(nurse, on='HADM_ID')

In [23]:
rad_df.shape

(1346, 12)

In [24]:
pis_df.shape

(266, 12)

In [27]:
nurse_df.shape

(267, 12)

In [42]:
rad_df = rad_df[['HADM_ID','TEXT', 'Obesity', 'Advanced.Heart.Disease', 'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression'
       ]]

In [33]:
pis_df = pis_df[['HADM_ID','TEXT', 'Obesity', 'Advanced.Heart.Disease', 'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression'
       ]]

In [34]:
nurse_df = nurse_df[['HADM_ID','TEXT', 'Obesity', 'Advanced.Heart.Disease', 'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression'
       ]]

In [36]:
pis_df.columns

Index(['HADM_ID', 'TEXT', 'Obesity', 'Advanced.Heart.Disease',
       'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression'],
      dtype='object')

In [44]:
rad_df.to_csv(os.path.join(files_dir, 'pheno_rad-ref.csv'),index=False)

In [38]:
pis_df.to_csv(os.path.join(files_dir, 'pheno_pis-ref.csv'),index=False)

In [39]:
nurse_df.to_csv(os.path.join(files_dir, 'pheno_nurse-ref.csv'),index=False)

In [43]:
rad_df.columns


Index(['HADM_ID', 'TEXT', 'Obesity', 'Advanced.Heart.Disease',
       'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression'],
      dtype='object')

In [28]:
df.iloc[0].TEXT

'admission date discharge date date birth sex service medicine allergies percocet bactrim ds lisinopril attending chief complaint hypotension major surgical invasive procedure none history present illness mr yo w multiple sclerosis seizure disorder presented osh delusions ams x days osh noted na history hyponatremia na mid since seen nephrology osh approx sec generalized tonic clonic seizure received mg ativan transferred ed also history seizures especially setting infection hyponatremia unclear seizures without inciting event currently weaned keppra gabapentin started tegretol er vs l given l ns given ams setting infection known chronic utis indwelling suprapubic catheter neurogenic bladder blood urine cultures obtained well cxr urine culture grew pseudomonas cxr showed possible infiltrate treated vancomycin cefepime head ct negative past medical history ms since progressive quadriplegic neurogenic bladder suprapubic catheter restrictive pft history aspiration pnas esophageal ulcer ns

In [29]:
df.iloc[1].TEXT

'admission date discharge date date birth sex f service cardiothoracic surgery chief complaint shortness breath exertion history present illness patient history woman history hypertension hyperlipidemia congestive heart failure rheumatic heart disease paroxysmal atrial fibrillation admitted cardioversion rapid atrial fibrillation admission transesophageal echocardiogram showed ejection fraction aortic insufficiency mitral regurgitation tricuspid regurgitation small pleural cardiac effusion echocardiogram unchanged previous echocardiogram underwent cardiac catheterization anticipation future cardiac surgery catheterization showed left main left anterior descending circumflex om1 right coronary artery please see catheterization report full details admitted directly operating room coronary artery bypass grafting mitral valve replacement postoperative admission past medical history rheumatic heart disease congestive heart failure hypertension hypercholesterolemia paroxysmal atrial fibrilla

In [25]:
df.to_csv(os.path.join(files_dir, 'pheno_disch-ref.csv'),index=False)

In [16]:
df.columns

Index(['HADM_ID', 'Obesity', 'Advanced.Heart.Disease', 'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression',
       'TEXT'],
      dtype='object')

In [107]:
notes1 = pd.read_csv(os.path.join(files_dir, 'notes_nurse.csv'))

In [108]:
df = pheno.merge(notes1, on='HADM_ID')

In [55]:
pheno.rename(columns={'Hospital.Admission.ID':'HADM_ID'}, inplace=True)
df = notes1.merge(pheno, on='HADM_ID')

In [56]:
df

HADM_ID                                               TEXT  SUBJECT_ID  \
0     100103.0  pm chest pa lat clip reason f u admitting diag...        3365   
1     100103.0  pm chest pa lat clip reason f u admitting diag...        3365   
2     100473.0  chest portable ap clip reason please assess in...        5525   
3     100473.0  chest portable ap clip reason please assess in...        5525   
4     100548.0  pm hip unilat min views left clip reason pleas...        2265   
...        ...                                                ...         ...   
1853  199652.0  ercp biliary pancreas gi unit clip reason bile...        6833   
1854  199807.0  pm chest portable ap physician reason eval pla...       23549   
1855  199807.0  pm chest portable ap physician reason eval pla...       23549   
1856  199883.0  pm chest pa lat clip reason pneumonia admittin...        7029   
1857  199883.0  pm chest pa lat clip reason pneumonia admittin...        7029   

      ROW_ID  ADVANCED.CANCER  ADVANCED.HEART.DISEASE  ADVANCED.LUNG.DISEASE  \
0      17170                0                       0                      0   
1      17170                0                       0                      0   
2      52670                0                       0                      0   
3      52670                0                       0                      0   
4      21117                0                       0                      0   
...      ...              ...                     ...                    ...   
1853   30543                0                       0                      0   
1854    2787                0                       1                      1   
1855    2787                0                       1                      1   
1856   18731                0                       0                      0   
1857   18731                0                       0                      0   

      ALCOHOL.ABUSE BATCH.ID  CHRONIC.NEUROLOGICAL.DYSTROPHIES  ...  DEMENTIA  \
0                 0  08Apr16                                 0  ...         0   
1                 0  08Apr16                                 0  ...         0   
2                 0  18Feb16                                 0  ...         0   
3                 0  05Oct16                                 0  ...         0   
4                 0  08Apr16                                 0  ...         0   
...             ...      ...                               ...  ...       ...   
1853              0  16Mar16                                 0  ...         0   
1854              0  07Dec15                                 0  ...         0   
1855              0  07Dec15                                 0  ...         0   
1856              1  18Feb16                                 0  ...         0   
1857              1  18Feb16                                 0  ...         0   

      DEPRESSION  DEVELOPMENTAL.DELAY.RETARDATION  NON.ADHERENCE  NONE  \
0              0                                0              0     1   
1              0                                0              0     1   
2              0                                0              0     1   
3              0                                0              0     0   
4              0                                0              0     1   
...          ...                              ...            ...   ...   
1853           1                                0              0     1   
1854           0                                0              0     0   
1855           0                                0              0     0   
1856           0                                0              1     0   
1857           0                                0              1     0   

      OBESITY  OPERATOR OTHER.SUBSTANCE.ABUSE  \
0           0       JTW                     0   
1           0       ETM                     0   
2           0        JW                     0   
3           1  

In [109]:
columns_titles = ['HADM_ID', 'TEXT', 'Obesity', 'Advanced.Heart.Disease',
       'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression'
       ]
df=df.reindex(columns=columns_titles)

In [110]:
df.columns

Index(['HADM_ID', 'TEXT', 'Obesity', 'Advanced.Heart.Disease',
       'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression'],
      dtype='object')

In [111]:
notes2 = pd.read_csv(os.path.join(files_dir, 'notes_disch.csv'))

In [112]:
df = df.merge(notes2, on='HADM_ID')

In [113]:
df.shape

(218, 13)

In [114]:
df.columns

Index(['HADM_ID', 'TEXT_x', 'Obesity', 'Advanced.Heart.Disease',
       'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression',
       'TEXT_y'],
      dtype='object')

In [115]:
df = df[['HADM_ID', 'TEXT_x', 'TEXT_y','Obesity', 'Advanced.Heart.Disease',
       'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression'
       ]]

In [116]:
df.shape

(218, 13)

In [124]:
df

HADM_ID                                             TEXT_x  \
0     100485  history left lower extremity claudication seve...   
1     100485  history left lower extremity claudication seve...   
2     102607  pt esrd hd cv issues afib chf pvd sp aka amput...   
3     102607  pt esrd hd cv issues afib chf pvd sp aka amput...   
4     103002  69 yrold rll nsclc squamous resected positive ...   
..       ...                                                ...   
213   198393  year old lady adm r last evening home pt exper...   
214   198393  year old lady adm r last evening home pt exper...   
215   198393  year old lady adm r last evening home pt exper...   
216   198781  events overnight received additional l ivf mai...   
217   198781  events overnight received additional l ivf mai...   

                                                TEXT_y  Obesity  \
0    admission date discharge date date birth sex f...      NaN   
1    admission date discharge date date birth sex f...      NaN   
2    admission date discharge date date birth sex f...      NaN   
3    admission date discharge date date birth sex f...      NaN   
4    admission date discharge date date birth sex f...      NaN   
..                                                 ...      ...   
213  admission date discharge date service medicine...      NaN   
214  admission date discharge date service medicine...      NaN   
215  admission date discharge date service medicine...      NaN   
216  admission date discharge date date birth sex s...      NaN   
217  admission date discharge date date birth sex s...      NaN   

     Advanced.Heart.Disease  Advanced.Lung.Disease  \
0                       NaN                    NaN   
1                       NaN                    NaN   
2                       NaN                    NaN   
3                       NaN                    NaN   
4                       NaN                    NaN   
..                      ...                    ...   
213                     NaN                    NaN   
214                     NaN                    NaN   
215                     NaN                    NaN   
216                     NaN                    NaN   
217                     NaN                    NaN   

     Schizophrenia.and.other.Psychiatric.Disorders  Alcohol.Abuse  \
0                                              NaN            NaN   
1                                              NaN            NaN   
2                                              NaN            NaN   
3                                              NaN            NaN   
4                                              NaN            NaN   
..                                             ...            ...   
213                                            NaN            NaN   
214                                            NaN            NaN   
215                                            NaN            NaN   
216                                            NaN            NaN   
217                                            NaN            NaN   

     Other.Substance.Abuse  Chronic.Pain.Fibromyalgia  \
0                      NaN                        NaN   
1                      NaN                        NaN   
2                      NaN                        NaN   
3                      NaN                        NaN   
4                      NaN                        NaN   
..                     ...                        ...   
213                    NaN                        NaN   
214                    NaN                        NaN   
215                    NaN                        NaN   
216                    NaN                        NaN   
217                    NaN                        NaN   

     Chronic.Neurological.Dystrophies  Advanced.Cancer  Depression  
0                                 NaN              NaN         NaN  
1                                 NaN              NaN         NaN  
2                        

In [117]:
df.to_csv(os.path.join(files_dir, 'pheno-nurse-disch.csv'),index=False)

In [120]:
d = pd.read_csv(os.path.join(files_dir, 'pheno_disch_rad.csv'))

In [121]:
d.shape

(641, 13)

In [40]:
text1 = notes1.TEXT.tolist()
text = notes.TEXT.tolist()

In [41]:
s2 = " ".join(text)
s1 = " ".join(text1)
s = s1+ " " + s2
with open("./disch_rad_notes.txt", 'w') as f:
    f.write(s)

In [14]:
pheno.columns

Index(['HADM_ID', 'Obesity', 'Advanced.Heart.Disease', 'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression'],
      dtype='object')

In [23]:
disch = pd.read_csv(os.path.join(files_dir, 'notes_disch.csv'))

In [24]:
d = df.merge(disch,on='HADM_ID')

In [25]:
d.columns

Index(['HADM_ID', 'TEXT_x', 'Obesity', 'Advanced.Heart.Disease',
       'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression',
       'TEXT_y'],
      dtype='object')

In [18]:
columns_titles = ['HADM_ID', 'TEXT_x','TEXT_y', 'Obesity', 'Advanced.Heart.Disease',
       'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression'
       ]
df=df.reindex(columns=columns_titles)

In [19]:
df.columns

Index(['HADM_ID', 'TEXT_x', 'TEXT_y', 'Obesity', 'Advanced.Heart.Disease',
       'Advanced.Lung.Disease',
       'Schizophrenia.and.other.Psychiatric.Disorders', 'Alcohol.Abuse',
       'Other.Substance.Abuse', 'Chronic.Pain.Fibromyalgia',
       'Chronic.Neurological.Dystrophies', 'Advanced.Cancer', 'Depression'],
      dtype='object')

In [21]:
df.to_csv(os.path.join(files_dir, 'pheno_disch_rad-ref.csv'),index=False)

In [5]:
len(notes['NOTES'].min())

37991

In [19]:
field_length = notes.TEXT.astype(str).map(len)
#print(notes.loc[field_length.argmax(), 'NOTES'])
sm = notes.loc[field_length.argmin(), 'TEXT']
lg = notes.loc[field_length.argmax(), 'TEXT']

print(len(sm),len(lg))

153 51779


In [21]:
text = notes['TEXT'].tolist()
avg = sum(map(len, text))/float(len(text))

In [22]:
avg

6790.64892083602

In [19]:
notes1

HADM_ID                                               TEXT
0      100001.0  chest pa lat clip reason eval infiltrate medic...
1      100003.0  pm liver gallbladder us single organ clip reas...
2      100006.0  chest portable ap clip reason please assess in...
3      100009.0  pm chest pa lat clip reason pre op admitting d...
4      100010.0  pm chest portable ap different physician reaso...
...         ...                                                ...
45521  199993.0  chest portable ap clip reason r effusion medic...
45522  199994.0  pm chest portable ap clip reason pt self extub...
45523  199995.0  pm abdomen u complete study duplex dopp abd pe...
45524  199998.0  pm chest port line placement clip reason line ...
45525  199999.0  chest portable ap clip reason interval change ...

[45526 rows x 2 columns]

In [20]:
df = notes.merge(pheno, on='HADM_ID')

In [39]:
df = df[['HADM_ID', 'TEXT','ADVANCED.CANCER', 'ADVANCED.HEART.DISEASE',
       'ADVANCED.LUNG.DISEASE', 'ALCOHOL.ABUSE',
       'CHRONIC.NEUROLOGICAL.DYSTROPHIES', 'CHRONIC.PAIN.FIBROMYALGIA',
       'DEPRESSION', 'OBESITY', 'OTHER.SUBSTANCE.ABUSE',
       'SCHIZOPHRENIA.AND.OTHER.PSYCHIATRIC.DISORDERS']]

In [21]:
df

HADM_ID                                               TEXT  \
0    100103.0  admission date discharge date date birth sex f...   
1    100137.0  admission date discharge date date birth sex s...   
2    100473.0  admission date discharge date date birth sex s...   
3    100485.0  admission date discharge date date birth sex f...   
4    100548.0  admission date discharge date date birth sex s...   
..        ...                                                ...   
808  199576.0  admission date discharge date date birth sex s...   
809  199652.0  admission date discharge date date birth sex f...   
810  199807.0  admission date discharge date date birth sex f...   
811  199883.0  admission date discharge date date birth sex s...   
812  199884.0  admission date discharge date date birth sex s...   

     ADVANCED.CANCER  ADVANCED.HEART.DISEASE  ADVANCED.LUNG.DISEASE  \
0                  0                       0                      0   
1                  0                       0                      0   
2                  0                       0                      0   
3                  0                       0                      0   
4                  0                       0                      0   
..               ...                     ...                    ...   
808                0                       0                      0   
809                1                       0                      0   
810                0                       1                      1   
811                0                       0                      0   
812                0                       1                      0   

     ALCOHOL.ABUSE  CHRONIC.NEUROLOGICAL.DYSTROPHIES  \
0                0                                 0   
1                0                                 0   
2                0                                 0   
3                0                                 0   
4                0                                 1   
..             ...                               ...   
808              0                                 0   
809              0                                 0   
810              0                                 0   
811              1                                 0   
812              0                                 0   

     CHRONIC.PAIN.FIBROMYALGIA  DEPRESSION  OBESITY  OTHER.SUBSTANCE.ABUSE  \
0                            0           0        0                      0   
1                            0           0        0                      0   
2                            0           0        1                      0   
3                            0           1        0                      0   
4                            0           0        0                      0   
..                         ...         ...      ...                    ...   
808                          0           0        0                      0   
809                          0           1        0                      0   
810                          0           0        0                      0   
811                          0           0        0                      0   
812                          0           1        0                      0   

     SCHIZOPHRENIA.AND.OTHER.PSYCHIATRIC.DISORDERS  
0                                                0  
1                                                0  
2                                                0  
3                                                1  
4                                                0  
..                                             ...  
808                                              0  
809                                              0  
810                                              0  
811                                              0  
812                                              0  

[813 rows x 12 columns]

In [22]:
df1 = notes1.merge(pheno, on='HADM_ID')

In [20]:
notes1 = pd.read_csv(os.path.join(files_dir, 'nurse_phys.csv'))

In [22]:
df1 = df1[['HADM_ID', 'NOTES', 'ADVANCED.CANCER', 'ADVANCED.HEART.DISEASE',
       'ADVANCED.LUNG.DISEASE', 'ALCOHOL.ABUSE',
       'CHRONIC.NEUROLOGICAL.DYSTROPHIES', 'CHRONIC.PAIN.FIBROMYALGIA',
       'DEMENTIA', 'DEPRESSION', 'DEVELOPMENTAL.DELAY.RETARDATION',
       'NON.ADHERENCE', 'NONE', 'OBESITY', 'OTHER.SUBSTANCE.ABUSE',
       'SCHIZOPHRENIA.AND.OTHER.PSYCHIATRIC.DISORDERS']]

In [23]:
df1

HADM_ID                                               TEXT  \
0    100103.0  pm chest pa lat clip reason f u admitting diag...   
1    100473.0  chest portable ap clip reason please assess in...   
2    100548.0  pm hip unilat min views left clip reason pleas...   
3    100654.0  chest portable ap clip reason eval pna effusio...   
4    100960.0  pm chest pa lat clip reason infiltrate medical...   
..        ...                                                ...   
636  199365.0  pm ct head w contrast clip reason ms changes h...   
637  199576.0  pm chest portable ap clip reason r pneumothora...   
638  199652.0  ercp biliary pancreas gi unit clip reason bile...   
639  199807.0  pm chest portable ap physician reason eval pla...   
640  199883.0  pm chest pa lat clip reason pneumonia admittin...   

     ADVANCED.CANCER  ADVANCED.HEART.DISEASE  ADVANCED.LUNG.DISEASE  \
0                  0                       0                      0   
1                  0                       0                      0   
2                  0                       0                      0   
3                  0                       0                      0   
4                  0                       0                      1   
..               ...                     ...                    ...   
636                0                       1                      0   
637                0                       0                      0   
638                1                       0                      0   
639                0                       1                      1   
640                0                       0                      0   

     ALCOHOL.ABUSE  CHRONIC.NEUROLOGICAL.DYSTROPHIES  \
0                0                                 0   
1                0                                 0   
2                0                                 1   
3                1                                 0   
4                0                                 0   
..             ...                               ...   
636              0                                 0   
637              0                                 0   
638              0                                 0   
639              0                                 0   
640              1                                 0   

     CHRONIC.PAIN.FIBROMYALGIA  DEPRESSION  OBESITY  OTHER.SUBSTANCE.ABUSE  \
0                            0           0        0                      0   
1                            0           0        1                      0   
2                            0           0        0                      0   
3                            0           0        0                      0   
4                            0           0        0                      0   
..                         ...         ...      ...                    ...   
636                          0           1        0                      0   
637                          0           0        0                      0   
638                          0           1        0                      0   
639                          0           0        0                      0   
640                          0           0        0                      0   

     SCHIZOPHRENIA.AND.OTHER.PSYCHIATRIC.DISORDERS  
0                                                0  
1                                                0  
2                                                0  
3                                                0  
4                                                1  
..                                             ...  
636                                              0  
637                                              0  
638                                              0  
639                                              0  
640                                              0  

[641 rows x 12 columns]

In [57]:
df1.to_csv(os.path.join(files_dir, 'pheno_disch_rad.csv'), index=False)

In [3]:
df1 = pd.read_csv(os.path.join(files_dir, 'pheno_disch_rad.csv'))

In [6]:
df1.sum(axis=0)

HADM_ID                                                                                9.63329e+07
TEXT_x                                           pm chest pa lat clip reason f u admitting diag...
TEXT_y                                           admission date discharge date date birth sex f...
ADVANCED.CANCER                                                                                 59
ADVANCED.HEART.DISEASE                                                                         145
ADVANCED.LUNG.DISEASE                                                                           83
ALCOHOL.ABUSE                                                                                   90
CHRONIC.NEUROLOGICAL.DYSTROPHIES                                                               153
CHRONIC.PAIN.FIBROMYALGIA                                                                      126
DEPRESSION                                                                                     195
OBESITY   

In [25]:
df1.tail(2)

HADM_ID                                               TEXT  \
639  199807.0  pm chest portable ap physician reason eval pla...   
640  199883.0  pm chest pa lat clip reason pneumonia admittin...   

     ADVANCED.CANCER  ADVANCED.HEART.DISEASE  ADVANCED.LUNG.DISEASE  \
639                0                       1                      1   
640                0                       0                      0   

     ALCOHOL.ABUSE  CHRONIC.NEUROLOGICAL.DYSTROPHIES  \
639              0                                 0   
640              1                                 0   

     CHRONIC.PAIN.FIBROMYALGIA  DEPRESSION  OBESITY  OTHER.SUBSTANCE.ABUSE  \
639                          0           0        0                      0   
640                          0           0        0                      0   

     SCHIZOPHRENIA.AND.OTHER.PSYCHIATRIC.DISORDERS  
639                                              0  
640                                              0

In [26]:
dd = df.tail(2)['TEXT'].tolist()
dd[0]

'admission date discharge date date birth sex service medicine allergies patient recorded known allergies drugs attending chief complaint alcohol intoxication diabetic ketoacidosis major surgical invasive procedure none history present illness year old male poorly controlled type diabetes presents found sleeping sidewalk critically high glucose evidence alcohol intoxication ed glucose anion gap urine ketones head ct negative acute bleed started insulin drip admitted icu management time admission mildly responsive limiting history note prior admissions dka past medical history dm insulin dependent p mva social history construction worker illegal resident us denies smoking etoh illicit drugs family family history dm cad cancer physical exam physical exam admission vitals temp bp pulse resp l nc gen nad lying bed asleep arousable heent perrla anicteric sclera dry mucous membranes neck supple op clear lad cardiac rrr nl s1 s2 r g jvd pulmonary distant breath sounds wheezes rhonci rales abd

In [27]:
dr = df1.tail(1)['TEXT'].tolist()
dr[0]

'pm chest pa lat clip reason pneumonia admitting diagnosis diabetic ketoacidosis medical condition year old man fever reason examination pneumonia final report two view chest x ray indication fever comparison heart size normal recently reported right basilar opacity nearly resolved right pleural effusion resolved new areas abnormality impression rapidly resolving right basilar opacity time course favors atelectasis aspiration infectious pneumonia chest portable ap clip reason r consolidations effusions admitting diagnosis diabetic ketoacidosis medical condition year old man found dka etoh intoxication reports cough subjective fevers prior presentation r pna reason examination r consolidations effusions final report study ap chest history year old man dka alcohol intoxication patient cough subjective fevers findings comparison made previous study cardiac silhouette mediastinum unremarkable small right sided pleural effusion right basilar subsegmental atelectasis evidence pulmonary edema

In [11]:
l = df.sum(axis=0).tolist()

In [18]:
l[2:]

[72, 184, 105, 110, 205, 160, 240, 60, 78, 144]

In [13]:
x = l[2:]

In [15]:
x = [1-(i/813) for i in x]

In [16]:
x

[0.9114391143911439,
 0.7736777367773677,
 0.8708487084870848,
 0.8646986469864699,
 0.7478474784747847,
 0.8031980319803198,
 0.7047970479704797,
 0.9261992619926199,
 0.9040590405904059,
 0.8228782287822878]

In [34]:
df = pd.read_csv(os.path.join(files_dir, 'pheno_disch-ref.csv'))

In [35]:
df

HADM_ID                                               TEXT  Obesity  \
0     100020.0  admission date discharge date date birth sex s...        0   
1     100103.0  admission date discharge date date birth sex f...        0   
2     100137.0  admission date discharge date date birth sex s...        0   
3     100177.0  admission date discharge date date birth sex s...        0   
4     100473.0  admission date discharge date date birth sex s...        1   
...        ...                                                ...      ...   
1604  199807.0  admission date discharge date date birth sex f...        0   
1605  199828.0  admission date discharge date date birth sex s...        0   
1606  199883.0  admission date discharge date date birth sex s...        0   
1607  199884.0  admission date discharge date date birth sex s...        0   
1608  199999.0  admission date discharge date service medicine...        0   

      Advanced.Heart.Disease  Advanced.Lung.Disease  \
0                          0                      0   
1                          0                      0   
2                          0                      0   
3                          0                      0   
4                          0                      0   
...                      ...                    ...   
1604                       1                      1   
1605                       0                      1   
1606                       0                      0   
1607                       1                      0   
1608                       0                      0   

      Schizophrenia.and.other.Psychiatric.Disorders  Alcohol.Abuse  \
0                                                 0              0   
1                                                 0              0   
2                                                 0              0   
3                                                 0              0   
4                                                 0              0   
...                                             ...            ...   
1604                                              0              0   
1605                                              0              1   
1606                                              0              1   
1607                                              0              0   
1608                                              0              0   

      Other.Substance.Abuse  Chronic.Pain.Fibromyalgia  \
0                         0                          1   
1                         0                          0   
2                         0                          0   
3                         0                          0   
4                         0                          0   
...                     ...                        ...   
1604                      0                          0   
1605                      0                          0   
1606                      0                          0   
1607                      0                          0   
1608                      0                          0   

      Chronic.Neurological.Dystrophies  Advanced.Cancer  Depression  
0                                    1                0           0  
1                                    0                0           0  
2                                    0                0           0  
3                                    0                0           0  
4                                    0                0           0  
...                                ...              ...         ...  
1604                                 0                0           0  
1605                                 1                0           0  
1606                                 0                0           0  
1607                                 0                0           1  
1608                                 0                0           0  

[1609 rows x 12 columns]

In [36]:
l = list(df.TEXT)


In [37]:
l

['admission date discharge date date birth sex service medicine allergies percocet bactrim ds lisinopril attending chief complaint hypotension major surgical invasive procedure none history present illness mr yo w multiple sclerosis seizure disorder presented osh delusions ams x days osh noted na history hyponatremia na mid since seen nephrology osh approx sec generalized tonic clonic seizure received mg ativan transferred ed also history seizures especially setting infection hyponatremia unclear seizures without inciting event currently weaned keppra gabapentin started tegretol er vs l given l ns given ams setting infection known chronic utis indwelling suprapubic catheter neurogenic bladder blood urine cultures obtained well cxr urine culture grew pseudomonas cxr showed possible infiltrate treated vancomycin cefepime head ct negative past medical history ms since progressive quadriplegic neurogenic bladder suprapubic catheter restrictive pft history aspiration pnas esophageal ulcer n

In [38]:
len(l)

1609

In [43]:
length = []
for i in l:
    length.append(len(i.split()))

In [44]:
min(length)

52

In [45]:
max(length)

5341

In [48]:
np.mean(length)

1104.9509011808577